## Download the data

In [1]:
!wget "https://www.dropbox.com/scl/fi/vs18rypduppjv4ywye2f2/train_dataset_train_data_Mediawise.zip?rlkey=3b10en8rbsdglcbiuwcydwpp6&st=vbeiqkz3&dl=0" -O data.zip

--2024-07-07 03:30:57--  https://www.dropbox.com/scl/fi/vs18rypduppjv4ywye2f2/train_dataset_train_data_Mediawise.zip?rlkey=3b10en8rbsdglcbiuwcydwpp6&st=vbeiqkz3&dl=0
Resolving www.dropbox.com (www.dropbox.com)... 162.125.4.18, 2620:100:601d:18::a27d:512
Connecting to www.dropbox.com (www.dropbox.com)|162.125.4.18|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://uc140c3a77527cc54d1f148b2300.dl.dropboxusercontent.com/cd/0/inline/CWNxR_wRcUftx_JFb4Z4TlEjk3eiRUV_RV8ID6Z1oXn4AJEYb12tYAQ5H-ClxbzE786JL2VBEXiQu0DN5oO-tlidITKcDSyxJzJ7eAZnYoAvix0bZ_FYzcJEOK0bmedcpW9sC0UKQTM7mbiUAqH1Yzg2/file# [following]
--2024-07-07 03:30:57--  https://uc140c3a77527cc54d1f148b2300.dl.dropboxusercontent.com/cd/0/inline/CWNxR_wRcUftx_JFb4Z4TlEjk3eiRUV_RV8ID6Z1oXn4AJEYb12tYAQ5H-ClxbzE786JL2VBEXiQu0DN5oO-tlidITKcDSyxJzJ7eAZnYoAvix0bZ_FYzcJEOK0bmedcpW9sC0UKQTM7mbiUAqH1Yzg2/file
Resolving uc140c3a77527cc54d1f148b2300.dl.dropboxusercontent.com (uc140c3a77527cc54d1f148b2300.dl.drop

In [2]:
!unzip data.zip

Archive:  data.zip
   creating: train_data_Mediawise/
  inflating: train_data_Mediawise/readme.md  
  inflating: __MACOSX/train_data_Mediawise/._readme.md  
  inflating: train_data_Mediawise/baseline.ipynb  
  inflating: __MACOSX/train_data_Mediawise/._baseline.ipynb  
  inflating: train_data_Mediawise/train_data.json  


In [8]:
!wget "https://www.dropbox.com/scl/fi/zr56s2f0zu0ocqygoyxb4/df.csv?rlkey=37o5r6bre9te6kaslgm0fupf0&st=ndg5vx6p&dl=0" -O df.csv

--2024-07-07 03:31:56--  https://www.dropbox.com/scl/fi/zr56s2f0zu0ocqygoyxb4/df.csv?rlkey=37o5r6bre9te6kaslgm0fupf0&st=ndg5vx6p&dl=0
Resolving www.dropbox.com (www.dropbox.com)... 162.125.80.18, 2620:100:6019:18::a27d:412
Connecting to www.dropbox.com (www.dropbox.com)|162.125.80.18|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://uc9611d89e2568c83e4d1112ca7b.dl.dropboxusercontent.com/cd/0/inline/CWOHlxio6B0YP9fvj88_HRroyB1RkP9jOzuArnKsUKXrYiMMu5FNZugVgpdV6G_v3jwqsGckv-a7hgXY2Nx-NNWhMvSFLHSUyaH723pQ_AbwYt9v8Y4rQZnwBs7cAF0UfhFFNNNEUg58vTx_tan1AOkb/file# [following]
--2024-07-07 03:31:57--  https://uc9611d89e2568c83e4d1112ca7b.dl.dropboxusercontent.com/cd/0/inline/CWOHlxio6B0YP9fvj88_HRroyB1RkP9jOzuArnKsUKXrYiMMu5FNZugVgpdV6G_v3jwqsGckv-a7hgXY2Nx-NNWhMvSFLHSUyaH723pQ_AbwYt9v8Y4rQZnwBs7cAF0UfhFFNNNEUg58vTx_tan1AOkb/file
Resolving uc9611d89e2568c83e4d1112ca7b.dl.dropboxusercontent.com (uc9611d89e2568c83e4d1112ca7b.dl.dropboxusercontent.com)... 162.125

In [4]:
!pip install -q catboost

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.2/98.2 MB 4.7 MB/s eta 0:00:00


## Imports

In [149]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import torch

from catboost import CatBoostRegressor, CatBoostClassifier, Pool
from catboost import cv

from sklearn.model_selection import ShuffleSplit, train_test_split, GridSearchCV
from sklearn.neighbors import KNeighborsRegressor, NearestNeighbors
from sklearn.svm import SVR
from sklearn.linear_model import LinearRegression
from sklearn.neural_network import MLPRegressor
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error


SEED = 8642
np.random.seed(SEED)

config = {'min_xval':55.55, 'max_xval':55.95, 'min_yval':37.3, 'max_yval':37.9, 'x_ngroups': 8, 'y_ngroups': 8}

pd.set_option('display.max_columns', 100)
pd.set_option('display.max_rows', 100)

# Task 1

## Utils

In [6]:
def split_on_intervals(min_val, max_val, n):
    step = (max_val - min_val)/n
    intervals = [min_val+(step*x) for x in range(n+1)]
    return intervals


def create_groups(x_intervals, y_intervals):
    groups = {}
    x_intervals = np.concatenate([[-np.inf], x_intervals, [np.inf]])
    y_intervals = np.concatenate([[-np.inf], y_intervals, [np.inf]])
    for x_i in range(len(x_intervals)-1):
        for y_i in range(len(y_intervals)-1):
            groups[f'x : {x_intervals[x_i]} - {x_intervals[x_i+1]} | y : {y_intervals[y_i]} - {y_intervals[y_i+1]}'] = 0
    return groups


#Сортирует точки по регионам
def sort_on_groups(x_vals, y_vals, x_intervals, y_intervals, groups, only_vals = False):
    for x, y in zip(x_vals, y_vals):
        for x_i in range(len(x_intervals)-1):
            for y_i in range(len(y_intervals)-1):
                if ((x_intervals[x_i] <= x < x_intervals[x_i+1]) and (y_intervals[y_i] <= y < y_intervals[y_i+1])):
                    groups[f'x : {x_intervals[x_i]} - {x_intervals[x_i+1]} | y : {y_intervals[y_i]} - {y_intervals[y_i+1]}'] += 1

    if only_vals:
        return list(groups.values())

    return groups


def create_dataset(config, df):
    x_intervals = split_on_intervals(config['min_xval'], config['max_xval'], config['x_ngroups'])
    y_intervals = split_on_intervals(config['min_yval'], config['max_yval'], config['y_ngroups'])
    groups = create_groups(x_intervals, y_intervals)

    groups_values = []
    for i in range(len(df)):
        g = df.iloc[i]
        points = np.array([[float(x['lat']), float(x['lon'])] for x in g['points']])
        group_values = sort_on_groups(points[:,0], points[:,1], x_intervals, y_intervals, groups.copy(), only_vals = True)
        groups_values.append(group_values)

    groups_values = np.array(groups_values)
    for i in range(len(groups.keys())):
        groups[list(groups.keys())[i]]=groups_values[:,i]

    return groups


# def plot_fields(df, field_size, images_per_row = 5):

#     num_rows = len(df) // images_per_row + int(len(df) % images_per_row != 0)
#     fig, axes = plt.subplots(num_rows, images_per_row, figsize=(15, 3 * num_rows))


#     for i in range(num_rows * images_per_row):
#         if i < len(df):
#             ax = axes.flat[i]

#             data = df.iloc[i].values.reshape(field_size)


#             ax.imshow(data, cmap="Blues", interpolation='nearest')
#             ax.axis('off')


#             for i in range(field_size[0]):
#               for j in range(field_size[1]):
#                   text = ax.text(j, i, f'{data[i, j]}', ha='center', va='center', color='white')
#                   text.set_path_effects([path_effects.Stroke(linewidth=1, foreground='black'), path_effects.Normal()])


#         else:
#             axes.flat[i].axis('off')


#     plt.tight_layout()
#     plt.show()

In [132]:
def feature_engineering(df: pd.DataFrame, n_groups: int = 8, parse_json: bool = True, dists: bool = True,
                        age_feats: bool = True, normalize: bool = True, drop_zero_cols: bool = False,
                        process_points: bool = True) -> pd.DataFrame:

    df.reset_index(drop=True, inplace=True)

    if parse_json:
        df_norm = pd.concat([df, pd.json_normalize(df['targetAudience'])], axis=1)
        # print(df_norm)
        df_norm = df_norm.drop(columns=['targetAudience'])
    else:
        df_norm = df

    if process_points:
        df_norm['points_count'] = df_norm['points'].apply(len)
        if dists:
            lat_center = 55.7522
            lon_center = 37.6156
            # print(df_norm)
            df_norm['distance_center'] = df_norm['points'].apply(lambda points: [((float(point['lat']) - lat_center) ** 2 + (float(point['lon']) - lon_center) ** 2) ** 0.5 for point in points]).apply(sum) / df_norm['points_count']
            lat_patr = 55.763868
            lon_patr = 37.592168
            df_norm['distance_patriki'] = df_norm['points'].apply(lambda points: [((float(point['lat']) - lat_patr) ** 2 + (float(point['lon']) - lon_patr) ** 2) ** 0.5 for point in points]).apply(sum) / df_norm['points_count']
            lat_luzh = 55.717934
            lon_luzh = 37.551932
            df_norm['distance_luzhniki'] = df_norm['points'].apply(lambda points: [((float(point['lat']) - lat_luzh) ** 2 + (float(point['lon']) - lon_luzh) ** 2) ** 0.5 for point in points]).apply(sum) / df_norm['points_count']

        config = {'min_xval': 55.55, 'max_xval': 55.95, 'min_yval': 37.3, 'max_yval': 37.9, 'x_ngroups': 8, 'y_ngroups': 8}
        dataset = pd.DataFrame(create_dataset(config, df_norm))
        if drop_zero_cols:
            zero_columns = dataset.sum()[dataset.sum() == 0].index.tolist()
            dataset = dataset.drop(columns=zero_columns)
    else:
        dataset = pd.DataFrame()

    df_new = df_norm
    for col in ['hash', 'points', 'name']:
        try:
            df_new = df_new.drop(columns=[col])
        except: pass

    if age_feats:
        df_new['age_span'] = df_new.apply(lambda row: (row['ageTo'] - row['ageFrom']) ** 1/2, axis=1)
        df_new['age_mean'] = df_new.apply(lambda row: ((row['ageTo'] + row['ageFrom']) / 2) ** 1/2, axis=1)

    gender_ohe = pd.get_dummies(df_new['gender'])
    try:
        income_ohe = pd.get_dummies(df_new['income']).drop(columns=['ac'])
    except:
        print('no ac in income')
        income_ohe = pd.get_dummies(df_new['income'])

    df_full = pd.concat([dataset, df_new, gender_ohe, income_ohe], axis=1).drop(columns=['gender', 'income'])
    df_full = df_full.fillna(0)

    if normalize:
        df_scaled = (df_full - df_full.mean()) / df_full.std()
        df_scaled = df_scaled.fillna(0)
        return df_scaled
    else:
        return df_full


In [108]:
def fit_to_base_cols(df_scaled: pd.DataFrame, base_cols) -> pd.DataFrame:
    # base_df = pd.DataFrame(columns=base_cols)
    # for col in df_scaled.columns:
    #     base_df[col] = df_scaled[col]
    # base_df = base_df.fillna(0)
    missing_cols = list(set(base_cols.tolist()) - set(df_scaled.columns.tolist()))
    for col in missing_cols:
        df_scaled[col] = 0
    return df_scaled


def prep_test_df(test_df: pd.DataFrame, base_cols) -> pd.DataFrame:
    sc_df = feature_engineering(test_df, parse_json=True, normalize=False, drop_zero_cols=False)
    sc_df = fit_to_base_cols(sc_df, base_cols)
    return sc_df

In [109]:
def ensemble_inference(models, X_test):
    y_pred = np.zeros(len(X_test))
    for model in models[:]:
        y_pred += model.predict(X_test)
    y_pred /= len(models)
    return y_pred


def get_metrics(y_pred, y_test):
    rmse = mean_squared_error(y_test, y_pred, squared=False)
    r2 = r2_score(y_test, y_pred)
    mae = mean_absolute_error(y_test, y_pred)

    print(f'RMSE: {rmse:.4f}')
    print(f'R²: {r2:.4f}')
    print(f'MAE: {mae:.4f}')

## Read the data

### Read train data

In [156]:
df = pd.read_json('/content/train_data_Mediawise/train_data.json')
target = df.pop('value')
# df = pd.read_csv('df.csv').drop(columns=['Unnamed: 0'])
df

hash                                     targetAudience  \
0     41567f28db47bee7  {'name': 'All 25-45 BC', 'gender': 'all', 'age...   
1     94b6df335598a161  {'name': 'W 30-60', 'gender': 'female', 'ageFr...   
2     2ef4e73f0d2c51d0  {'name': 'W 30-60', 'gender': 'female', 'ageFr...   
3     b3ebb77f965de304  {'name': 'W 30+ BC', 'gender': 'female', 'ageF...   
4     76059b6cbb303166  {'name': 'W 30+ BC', 'gender': 'female', 'ageF...   
...                ...                                                ...   
1542  75563c4cce5ca6c0  {'name': 'All 30-55 BC', 'gender': 'all', 'age...   
1543  ed4353d7c33dd21c  {'name': '35-100 C', 'gender': 'all', 'ageFrom...   
1544  77a82843b71a77ec  {'name': '35-100 C', 'gender': 'all', 'ageFrom...   
1545  87b45be3fae91c39  {'name': 'M 25-55 ', 'gender': 'male', 'ageFro...   
1546  464e9e7d315ba25d  {'name': 'M 25-55 ', 'gender': 'male', 'ageFro...   

                                                 points  
0     [{'lat': '55.573691', 'lon': '37.631423', 'azi...  
1     [{'lat': '55.656665886902', 'lon': '37.7408534...  
2     [{'lat': '55.680953807163', 'lon': '37.6644265...  
3     [{'lat': '55.741072317672', 'lon': '37.6526972...  
4     [{'lat': '55.656665886902', 'lon': '37.7408534...  
...                                                 ...  
1542  [{'lat': '55.961879', 'lon': '37.333988', 'azi...  
1543  [{'lat': '55.752846850282', 'lon': '37.5875834...  
1544  [{'lat': '55.752846850282', 'lon': '37.5875834...  
1545  [{'lat': '55.662899746091', 'lon': '37.4817413...  
1546  [{'lat': '55.662899746091', 'lon': '37.4817413...  

[1547 rows x 3 columns]

In [158]:
df_scaled = feature_engineering(df,
                                parse_json=True,
                                drop_zero_cols=False,
                                process_points=False,  ###
                                normalize=False)  ############
base_cols = df_scaled.columns
base_df = pd.DataFrame(columns=base_cols)
base_df

Empty DataFrame
Columns: [ageFrom, ageTo, id, age_span, age_mean, all, female, male, ab, abc, bc, c]
Index: []

In [136]:
df_scaled

value  ageFrom  ageTo   id  age_span  age_mean    all  female   male  \
0     23.51       25     45  0.0      10.0     17.50   True   False  False   
1      1.20       30     60  0.0      15.0     22.50  False    True  False   
2      4.65       30     60  0.0      15.0     22.50  False    True  False   
3     32.09       30    100  0.0      35.0     32.50  False    True  False   
4     26.12       30    100  0.0      35.0     32.50  False    True  False   
...     ...      ...    ...  ...       ...       ...    ...     ...    ...   
1542  20.55       30     55  0.0      12.5     21.25   True   False  False   
1543  59.32       35    100  0.0      32.5     33.75   True   False  False   
1544  41.30       35    100  0.0      32.5     33.75   True   False  False   
1545  59.15       25     55  0.0      15.0     20.00  False   False   True   
1546  52.66       25     55  0.0      15.0     20.00  False   False   True   

         ab    abc     bc      c  
0     False  False   True  False  
1     False   True  False  False  
2     False   True  False  False  
3     False  False   True  False  
4     False  False   True  False  
...     ...    ...    ...    ...  
1542  False  False   True  False  
1543  False  False  False   True  
1544  False  False  False   True  
1545  False   True  False  False  
1546  False   True  False  False  

[1547 rows x 13 columns]

### Read and adapt test data

In [150]:
!wget "https://www.dropbox.com/scl/fi/y81u2l3nq92seyd326voe/test_data.json?rlkey=vcihvhi88la2zdwdsai88qfck&st=uhsy7zwo&dl=0" -O test_data.json

--2024-07-07 05:33:33--  https://www.dropbox.com/scl/fi/y81u2l3nq92seyd326voe/test_data.json?rlkey=vcihvhi88la2zdwdsai88qfck&st=uhsy7zwo&dl=0
Resolving www.dropbox.com (www.dropbox.com)... 162.125.4.18, 2620:100:6019:18::a27d:412
Connecting to www.dropbox.com (www.dropbox.com)|162.125.4.18|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://uc6c7a7f5c1edf481ab2807c31e8.dl.dropboxusercontent.com/cd/0/inline/CWP20HzFg0M5akSW4o6uL0LIAXZjmx0Cq92p2zlL2nhUW6izz7wivnu9zDdLL5HnjxJgCSCaVsDXXRmMB__XJ-d9_dXECvdwx0wTBoQCCd8vXPlbquoVjgz8UWiD1pvweMOljY2Fp-ZCmCNfK8T8icTc/file# [following]
--2024-07-07 05:33:33--  https://uc6c7a7f5c1edf481ab2807c31e8.dl.dropboxusercontent.com/cd/0/inline/CWP20HzFg0M5akSW4o6uL0LIAXZjmx0Cq92p2zlL2nhUW6izz7wivnu9zDdLL5HnjxJgCSCaVsDXXRmMB__XJ-d9_dXECvdwx0wTBoQCCd8vXPlbquoVjgz8UWiD1pvweMOljY2Fp-ZCmCNfK8T8icTc/file
Resolving uc6c7a7f5c1edf481ab2807c31e8.dl.dropboxusercontent.com (uc6c7a7f5c1edf481ab2807c31e8.dl.dropboxusercontent.com)... 1

In [131]:
df.iloc[234:235]

hash                                     targetAudience  \
234  4ca6b89578074737  {'name': 'All 18+', 'gender': 'all', 'ageFrom'...   

                                                points  
234  [{'lat': '55.788639320899', 'lon': '37.6793289...

In [159]:
source_test_df  = pd.read_json('/content/test_data.json')
test_df = prep_test_df(source_test_df, base_cols)
test_df

no ac in income


x : -inf - 55.55 | y : -inf - 37.3  x : -inf - 55.55 | y : 37.3 - 37.375  \
0                                     0                                     0   
1                                     0                                     0   
2                                     0                                     0   
3                                     0                                     0   
4                                     0                                     0   
..                                  ...                                   ...   
383                                   0                                     0   
384                                   0                                     0   
385                                   0                                     0   
386                                   0                                     0   
387                                   0                                     0   

     x : -inf - 55.55 | y : 37.375 - 37.449999999999996  \
0                                                    0    
1                                                    0    
2                                                    0    
3                                                    0    
4                                                    0    
..                                                 ...    
383                                                  0    
384                                                  0    
385                                                  0    
386                                                  0    
387                                                  0    

     x : -inf - 55.55 | y : 37.449999999999996 - 37.525  \
0                                                    0    
1                                                    0    
2                                                    0    
3                                                    0    
4                                                    0    
..                                                 ...    
383                                                  0    
384                                                  0    
385                                                  0    
386                                                  0    
387                                                  0    

     x : -inf - 55.55 | y : 37.525 - 37.599999999999994  \
0                                                    0    
1                                                    0    
2                                                    0    
3                                                    0    
4                                                    0    
..                                                 ...    
383                                                  0    
384                                                  0    
385                                                  0    
386                                                  0    
387                                                  0    

     x : -inf - 55.55 | y : 37.599999999999994 - 37.675  \
0                                                    0    
1                                                    0    
2                                                    0    
3                                                    0    
4                                                    0    
..                                                 ...    
383                                                  0    
384                                                  0    
385                                                  0    
386                                                  0    
387                                                  0    

     x : -inf - 55.55 | y : 37.675 - 37.75  \
0                                        0   
1                                        0   
2                                        0   
3           

In [160]:
test_df.sum()

x : -inf - 55.55 | y : -inf - 37.3                      0.0
x : -inf - 55.55 | y : 37.3 - 37.375                    0.0
x : -inf - 55.55 | y : 37.375 - 37.449999999999996      0.0
x : -inf - 55.55 | y : 37.449999999999996 - 37.525      0.0
x : -inf - 55.55 | y : 37.525 - 37.599999999999994      0.0
                                                      ...  
male                                                   23.0
ab                                                      4.0
abc                                                   130.0
bc                                                    219.0
c                                                      35.0
Length: 116, dtype: float64

## Feature engineering

### Add number of billboards as a feature

In [133]:
df_norm['points_count'] = df_norm['points'].apply(len)

### Add distances from billboards to key places in Moscow

In [134]:
lat_center = 55.7522
lon_center = 37.6156
df_norm['distance_center'] = df_norm['points'].apply(lambda points: [((float(point['lat']) - lat_center) ** 2 + (float(point['lon']) - lon_center) ** 2) ** 0.5 for point in points]).apply(sum) / df_norm['points_count']

In [135]:
lat_patr = 55.763868
lon_patr = 37.592168
df_norm['distance_patriki'] = df_norm['points'].apply(lambda points: [((float(point['lat']) - lat_patr) ** 2 + (float(point['lon']) - lon_patr) ** 2) ** 0.5 for point in points]).apply(sum) / df_norm['points_count']

In [136]:
lat_luzh = 55.717934
lon_luzh = 37.551932
df_norm['distance_luzhniki'] = df_norm['points'].apply(lambda points: [((float(point['lat']) - lat_luzh) ** 2 + (float(point['lon']) - lon_luzh) ** 2) ** 0.5 for point in points]).apply(sum) / df_norm['points_count']

In [137]:
df_norm

hash                                             points  \
0     41567f28db47bee7  [{'lat': '55.573691', 'lon': '37.631423', 'azi...   
1     94b6df335598a161  [{'lat': '55.656665886902', 'lon': '37.7408534...   
2     2ef4e73f0d2c51d0  [{'lat': '55.680953807163', 'lon': '37.6644265...   
3     b3ebb77f965de304  [{'lat': '55.741072317672', 'lon': '37.6526972...   
4     76059b6cbb303166  [{'lat': '55.656665886902', 'lon': '37.7408534...   
...                ...                                                ...   
1542  75563c4cce5ca6c0  [{'lat': '55.961879', 'lon': '37.333988', 'azi...   
1543  ed4353d7c33dd21c  [{'lat': '55.752846850282', 'lon': '37.5875834...   
1544  77a82843b71a77ec  [{'lat': '55.752846850282', 'lon': '37.5875834...   
1545  87b45be3fae91c39  [{'lat': '55.662899746091', 'lon': '37.4817413...   
1546  464e9e7d315ba25d  [{'lat': '55.662899746091', 'lon': '37.4817413...   

      value          name  gender  ageFrom  ageTo income  points_count  \
0     23.51  All 25-45 BC     all       25     45     bc            25   
1      1.20       W 30-60  female       30     60    abc            24   
2      4.65       W 30-60  female       30     60    abc            34   
3     32.09      W 30+ BC  female       30    100     bc           160   
4     26.12      W 30+ BC  female       30    100     bc            44   
...     ...           ...     ...      ...    ...    ...           ...   
1542  20.55  All 30-55 BC     all       30     55     bc            27   
1543  59.32      35-100 C     all       35    100      c            24   
1544  41.30      35-100 C     all       35    100      c            15   
1545  59.15      M 25-55     male       25     55    abc            37   
1546  52.66      M 25-55     male       25     55    abc            37   

      distance_center  distance_patriki  distance_luzhniki  
0            0.207695          0.207471           0.212658  
1            0.134828          0.136753           0.134529  
2            0.121927          0.122604           0.119879  
3            0.134150          0.134882           0.130684  
4            0.122182          0.123225           0.120970  
...               ...               ...                ...  
1542         0.241312          0.242313           0.251607  
1543         0.151788          0.136649           0.116366  
1544         0.192977          0.177750           0.146679  
1545         0.156199          0.151560           0.148901  
1546         0.156199          0.151560           0.148901  

[1547 rows x 12 columns]

### Split up into squares

In [138]:
config = {'min_xval':55.55, 'max_xval':55.95, 'min_yval':37.3, 'max_yval':37.9, 'x_ngroups': 8, 'y_ngroups': 8}

In [139]:
dataset = pd.DataFrame(create_dataset(config, df_norm))
dataset

x : -inf - 55.55 | y : -inf - 37.3  \
0                                      0   
1                                      0   
2                                      0   
3                                      0   
4                                      0   
...                                  ...   
1542                                   0   
1543                                   0   
1544                                   0   
1545                                   0   
1546                                   0   

      x : -inf - 55.55 | y : 37.3 - 37.375  \
0                                        0   
1                                        0   
2                                        0   
3                                        0   
4                                        0   
...                                    ...   
1542                                     0   
1543                                     0   
1544                                     0   
1545                                     0   
1546                                     0   

      x : -inf - 55.55 | y : 37.375 - 37.449999999999996  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.449999999999996 - 37.525  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.525 - 37.599999999999994  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.599999999999994 - 37.675  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.675 - 37

### Drop regions with sum = 0

In [140]:
zero_columns = dataset.sum()[dataset.sum() == 0].index.tolist()
zero_columns

['x : -inf - 55.55 | y : -inf - 37.3',
 'x : -inf - 55.55 | y : 37.3 - 37.375',
 'x : -inf - 55.55 | y : 37.375 - 37.449999999999996',
 'x : -inf - 55.55 | y : 37.449999999999996 - 37.525',
 'x : -inf - 55.55 | y : 37.525 - 37.599999999999994',
 'x : -inf - 55.55 | y : 37.599999999999994 - 37.675',
 'x : -inf - 55.55 | y : 37.675 - 37.75',
 'x : -inf - 55.55 | y : 37.75 - 37.824999999999996',
 'x : -inf - 55.55 | y : 37.824999999999996 - 37.9',
 'x : -inf - 55.55 | y : 37.9 - inf',
 'x : 55.55 - 55.599999999999994 | y : -inf - 37.3',
 'x : 55.55 - 55.599999999999994 | y : 37.824999999999996 - 37.9',
 'x : 55.55 - 55.599999999999994 | y : 37.9 - inf',
 'x : 55.599999999999994 - 55.65 | y : -inf - 37.3',
 'x : 55.599999999999994 - 55.65 | y : 37.9 - inf',
 'x : 55.65 - 55.7 | y : -inf - 37.3',
 'x : 55.65 - 55.7 | y : 37.9 - inf',
 'x : 55.7 - 55.75 | y : -inf - 37.3',
 'x : 55.7 - 55.75 | y : 37.9 - inf',
 'x : 55.75 - 55.8 | y : -inf - 37.3',
 'x : 55.75 - 55.8 | y : 37.9 - inf',
 'x :

In [141]:
dataset = dataset.drop(columns=zero_columns)
dataset

x : 55.55 - 55.599999999999994 | y : 37.3 - 37.375  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     2    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : 55.55 - 55.599999999999994 | y : 37.375 - 37.449999999999996  \
0                                                     0                  
1                                                     0                  
2                                                     0                  
3                                                     0                  
4                                                     0                  
...                                                 ...                  
1542                                                  0                  
1543                                                  0                  
1544                                                  0                  
1545                                                  0                  
1546                                                  0                  

      x : 55.55 - 55.599999999999994 | y : 37.449999999999996 - 37.525  \
0                                                     0                  
1                                                     0                  
2                                                     0                  
3                                                     1                  
4                                                     0                  
...                                                 ...                  
1542                                                  0                  
1543                                                  0                  
1544                                                  0                  
1545                                                  0                  
1546                                                  0                  

      x : 55.55 - 55.599999999999994 | y : 37.525 - 37.599999999999994  \
0                                                     0                  
1                                                     0                  
2                                                     0                  
3                                                     0                  
4                                                     0                  
...                                                 ...                  
1542                                                  0                  
1543                                                  0                  
1544                                                  0                  
1545                                                  0                  
1546                                                  0                  

      x : 55.55 - 55.599999999999994 | y : 37.599999999999994 - 37.675  \
0                                                     2                  
1                                                     0                  
2                                                     0                  
3                                                     0                  
4                                                     0                  
...                                                 ...                  
1542                                                  1                  
1543                      

### Remove columns that have already been processed

In [142]:
df_new = df_norm.drop(columns=['hash', 'points', 'name'])
df_new

value  gender  ageFrom  ageTo income  points_count  distance_center  \
0     23.51     all       25     45     bc            25         0.207695   
1      1.20  female       30     60    abc            24         0.134828   
2      4.65  female       30     60    abc            34         0.121927   
3     32.09  female       30    100     bc           160         0.134150   
4     26.12  female       30    100     bc            44         0.122182   
...     ...     ...      ...    ...    ...           ...              ...   
1542  20.55     all       30     55     bc            27         0.241312   
1543  59.32     all       35    100      c            24         0.151788   
1544  41.30     all       35    100      c            15         0.192977   
1545  59.15    male       25     55    abc            37         0.156199   
1546  52.66    male       25     55    abc            37         0.156199   

      distance_patriki  distance_luzhniki  
0             0.207471           0.212658  
1             0.136753           0.134529  
2             0.122604           0.119879  
3             0.134882           0.130684  
4             0.123225           0.120970  
...                ...                ...  
1542          0.242313           0.251607  
1543          0.136649           0.116366  
1544          0.177750           0.146679  
1545          0.151560           0.148901  
1546          0.151560           0.148901  

[1547 rows x 9 columns]

### Age feature engineering

In [143]:
df_new['age_span'] = df_new.apply(lambda row: (row['ageTo'] - row['ageFrom']) ** 1/2, axis=1)
df_new['age_mean'] = df_new.apply(lambda row: ((row['ageTo'] + row['ageFrom']) / 2) ** 1/2, axis=1)
df_new

value  gender  ageFrom  ageTo income  points_count  distance_center  \
0     23.51     all       25     45     bc            25         0.207695   
1      1.20  female       30     60    abc            24         0.134828   
2      4.65  female       30     60    abc            34         0.121927   
3     32.09  female       30    100     bc           160         0.134150   
4     26.12  female       30    100     bc            44         0.122182   
...     ...     ...      ...    ...    ...           ...              ...   
1542  20.55     all       30     55     bc            27         0.241312   
1543  59.32     all       35    100      c            24         0.151788   
1544  41.30     all       35    100      c            15         0.192977   
1545  59.15    male       25     55    abc            37         0.156199   
1546  52.66    male       25     55    abc            37         0.156199   

      distance_patriki  distance_luzhniki  age_span  age_mean  
0             0.207471           0.212658      10.0     17.50  
1             0.136753           0.134529      15.0     22.50  
2             0.122604           0.119879      15.0     22.50  
3             0.134882           0.130684      35.0     32.50  
4             0.123225           0.120970      35.0     32.50  
...                ...                ...       ...       ...  
1542          0.242313           0.251607      12.5     21.25  
1543          0.136649           0.116366      32.5     33.75  
1544          0.177750           0.146679      32.5     33.75  
1545          0.151560           0.148901      15.0     20.00  
1546          0.151560           0.148901      15.0     20.00  

[1547 rows x 11 columns]

### Label encoding

In [144]:
gender_ohe = pd.get_dummies(df_new['gender'])
income_ohe = pd.get_dummies(df_new['income']).drop(columns=['ac'])
income_ohe

ab    abc     bc      c
0     False  False   True  False
1     False   True  False  False
2     False   True  False  False
3     False  False   True  False
4     False  False   True  False
...     ...    ...    ...    ...
1542  False  False   True  False
1543  False  False  False   True
1544  False  False  False   True
1545  False   True  False  False
1546  False   True  False  False

[1547 rows x 4 columns]

In [145]:
df_full = pd.concat([df_new, dataset, gender_ohe, income_ohe], axis=1).drop(columns=['gender', 'income'])
target = df_full.pop('value')
df_full

ageFrom  ageTo  points_count  distance_center  distance_patriki  \
0          25     45            25         0.207695          0.207471   
1          30     60            24         0.134828          0.136753   
2          30     60            34         0.121927          0.122604   
3          30    100           160         0.134150          0.134882   
4          30    100            44         0.122182          0.123225   
...       ...    ...           ...              ...               ...   
1542       30     55            27         0.241312          0.242313   
1543       35    100            24         0.151788          0.136649   
1544       35    100            15         0.192977          0.177750   
1545       25     55            37         0.156199          0.151560   
1546       25     55            37         0.156199          0.151560   

      distance_luzhniki  age_span  age_mean  \
0              0.212658      10.0     17.50   
1              0.134529      15.0     22.50   
2              0.119879      15.0     22.50   
3              0.130684      35.0     32.50   
4              0.120970      35.0     32.50   
...                 ...       ...       ...   
1542           0.251607      12.5     21.25   
1543           0.116366      32.5     33.75   
1544           0.146679      32.5     33.75   
1545           0.148901      15.0     20.00   
1546           0.148901      15.0     20.00   

      x : 55.55 - 55.599999999999994 | y : 37.3 - 37.375  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     2    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : 55.55 - 55.599999999999994 | y : 37.375 - 37.449999999999996  ...  \
0                                                     0                 ...   
1                                                     0                 ...   
2                                                     0                 ...   
3                                                     0                 ...   
4                                                     0                 ...   
...                                                 ...                 ...   
1542                                                  0                 ...   
1543                                                  0                 ...   
1544                                                  0                 ...   
1545                                                  0                 ...   
1546                                                  0                 ...   

      x : 55.900000000000006 - 55.95 | y : 37.675 - 37.75  \
0                                                     0     
1                                                     0     
2                                                     0     
3                                                     0     
4                                                     0     
...                                                 ...     
1542                                                  0     
1543                                                  0     
1544                                                  0     
1545                                                  0     
1546                                                  0     

      x : 55.900000000000006 - 55.95 | y : 37.75 - 37.824999999999996  \
0                                                     0                 
1              

In [146]:
target

0       23.51
1        1.20
2        4.65
3       32.09
4       26.12
        ...  
1542    20.55
1543    59.32
1544    41.30
1545    59.15
1546    52.66
Name: value, Length: 1547, dtype: float64

In [147]:
df_scaled = (df_full - df_full.mean()) / df_full.std()
df_scaled

ageFrom     ageTo  points_count  distance_center  distance_patriki  \
0     0.052411 -0.854526     -0.462682         0.040671          0.040807   
1     0.833520 -0.148632     -0.469974        -0.050036         -0.047206   
2     0.833520 -0.148632     -0.397058        -0.066095         -0.064814   
3     0.833520  1.733753      0.521679        -0.050879         -0.049534   
4     0.833520  1.733753     -0.324142        -0.065778         -0.064041   
...        ...       ...           ...              ...               ...   
1542  0.833520 -0.383930     -0.448099         0.082519          0.084169   
1543  1.614630  1.733753     -0.469974        -0.028923         -0.047335   
1544  1.614630  1.733753     -0.535598         0.022351          0.003818   
1545  0.052411 -0.383930     -0.375183        -0.023432         -0.028778   
1546  0.052411 -0.383930     -0.375183        -0.023432         -0.028778   

      distance_luzhniki  age_span  age_mean  \
0              0.037611 -0.776246 -0.872346   
1             -0.059627 -0.356514  0.106560   
2             -0.077861 -0.356514  0.106560   
3             -0.064413  1.322412  2.064370   
4             -0.076503  1.322412  2.064370   
...                 ...       ...       ...   
1542           0.086087 -0.566380 -0.138167   
1543          -0.082233  1.112546  2.309096   
1544          -0.044506  1.112546  2.309096   
1545          -0.041740 -0.356514 -0.382893   
1546          -0.041740 -0.356514 -0.382893   

      x : 55.55 - 55.599999999999994 | y : 37.3 - 37.375  \
0                                             -0.120191    
1                                             -0.120191    
2                                             -0.120191    
3                                              9.414939    
4                                             -0.120191    
...                                                 ...    
1542                                          -0.120191    
1543                                          -0.120191    
1544                                          -0.120191    
1545                                          -0.120191    
1546                                          -0.120191    

      x : 55.55 - 55.599999999999994 | y : 37.375 - 37.449999999999996  ...  \
0                                             -0.056925                 ...   
1                                             -0.056925                 ...   
2                                             -0.056925                 ...   
3                                             -0.056925                 ...   
4                                             -0.056925                 ...   
...                                                 ...                 ...   
1542                                          -0.056925                 ...   
1543                                          -0.056925                 ...   
1544                                          -0.056925                 ...   
1545                                          -0.056925                 ...   
1546                                          -0.056925                 ...   

      x : 55.900000000000006 - 55.95 | y : 37.675 - 37.75  \
0                                             -0.096375     
1                                             -0.096375     
2                                             -0.096375     
3                                             -0.096375     
4                                             -0.096375     
...                                                 ...     
1542                                          -0.096375     
1543                                          -0.096375     
1544                                          -0.096375     
1545                                          -0.096375     
1546                                          -0.096375     

      x : 55.900000000000006 - 55.95 | y : 37.75 - 37.824999999999996  \
0                                        

## Final dataset

In [161]:
df_scaled = feature_engineering(df,
                                parse_json=True,
                                drop_zero_cols=False,
                                normalize=False)  ##################
df_scaled

x : -inf - 55.55 | y : -inf - 37.3  \
0                                      0   
1                                      0   
2                                      0   
3                                      0   
4                                      0   
...                                  ...   
1542                                   0   
1543                                   0   
1544                                   0   
1545                                   0   
1546                                   0   

      x : -inf - 55.55 | y : 37.3 - 37.375  \
0                                        0   
1                                        0   
2                                        0   
3                                        0   
4                                        0   
...                                    ...   
1542                                     0   
1543                                     0   
1544                                     0   
1545                                     0   
1546                                     0   

      x : -inf - 55.55 | y : 37.375 - 37.449999999999996  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.449999999999996 - 37.525  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.525 - 37.599999999999994  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.599999999999994 - 37.675  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.675 - 37

In [89]:
X = df_scaled
y = target

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=SEED)
X_val, X_test, y_val, y_test = train_test_split(X_test, y_test, test_size=0.52, random_state=SEED + 1)

In [339]:
models = []

## CatBoost

In [340]:
cb_model = CatBoostRegressor(iterations=5000,
                              max_depth=5,
                              l2_leaf_reg=3.0,
                              # learning_rate=0.05,
                              loss_function='RMSE',
                              random_seed=SEED)

cb_model.fit(X_train, y_train, eval_set=(X_val, y_val), verbose=100)
models.append(cb_model)

0:	learn: 23.3335991	test: 25.1740548	best: 25.1740548 (0)	total: 2.6ms	remaining: 13s
100:	learn: 11.0732358	test: 12.1209429	best: 12.1209429 (100)	total: 211ms	remaining: 10.2s
200:	learn: 9.2722644	test: 10.1329163	best: 10.1329163 (200)	total: 403ms	remaining: 9.62s
300:	learn: 8.2818964	test: 9.2224911	best: 9.2224911 (300)	total: 598ms	remaining: 9.33s
400:	learn: 7.4144083	test: 8.6925879	best: 8.6925879 (400)	total: 789ms	remaining: 9.04s
500:	learn: 6.7989032	test: 8.4681086	best: 8.4679743 (499)	total: 986ms	remaining: 8.86s
600:	learn: 6.3573774	test: 8.2705194	best: 8.2697844 (599)	total: 1.19s	remaining: 8.72s
700:	learn: 5.9407904	test: 8.1449116	best: 8.1446819 (698)	total: 1.37s	remaining: 8.43s
800:	learn: 5.6754429	test: 8.0266537	best: 8.0266537 (800)	total: 1.56s	remaining: 8.19s
900:	learn: 5.4101282	test: 7.9348568	best: 7.9339265 (896)	total: 1.76s	remaining: 8.03s
1000:	learn: 5.2270092	test: 7.8721755	best: 7.8720558 (999)	total: 2s	remaining: 7.97s
1100:	lear

In [341]:
y_pred = cb_model.predict(X_test)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 7.1234
R²: 0.9007
MAE: 4.7062


### CatBoost cross validation

In [342]:
from sklearn.model_selection import ShuffleSplit


params = dict(iterations=2000,
              max_depth=5,
              l2_leaf_reg=3.0,
              # learning_rate=0.05,
              loss_function='RMSE',
              random_seed=SEED)

train_pool = Pool(data=X, label=y)

shuffle_split = ShuffleSplit(n_splits=5, test_size=.25, random_state=SEED)
cv_data = cv(
    params = params,
    pool = train_pool,
    verbose = False,
    folds = shuffle_split,
    plot=True
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

Training on fold [0/5]

bestTest = 7.085604072
bestIteration = 1999

Training on fold [1/5]

bestTest = 7.707140455
bestIteration = 1901

Training on fold [2/5]

bestTest = 8.019219187
bestIteration = 1999

Training on fold [3/5]

bestTest = 7.2389994
bestIteration = 1998

Training on fold [4/5]

bestTest = 7.602343623
bestIteration = 1999



### CatBoost feature importances

In [345]:
pd.DataFrame({'feature_importance': cb_model.get_feature_importance(train_pool),
              'feature_names': X_val.columns}).sort_values(by=['feature_importance'],
                                                           ascending=False).head(60)

feature_importance                                      feature_names
2              8.248360                                       points_count
83             5.557064  x : 55.85 - 55.900000000000006 | y : 37.599999...
81             5.184285  x : 55.85 - 55.900000000000006 | y : 37.449999...
84             4.958818  x : 55.85 - 55.900000000000006 | y : 37.675 - ...
62             4.636934  x : 55.75 - 55.8 | y : 37.525 - 37.59999999999...
74             4.195192              x : 55.8 - 55.85 | y : 37.675 - 37.75
40             4.038686  x : 55.65 - 55.7 | y : 37.375 - 37.44999999999...
52             3.423696  x : 55.7 - 55.75 | y : 37.525 - 37.59999999999...
80             3.058299  x : 55.85 - 55.900000000000006 | y : 37.375 - ...
7              2.524348                                           age_mean
35             2.514284  x : 55.599999999999994 - 55.65 | y : 37.75 - 3...
31             2.501235  x : 55.599999999999994 - 55.65 | y : 37.449999...
24             2.446996  x : 55.55 - 55.599999999999994 | y : 37.675 - ...
64             2.085039              x : 55.75 - 55.8 | y : 37.675 - 37.75
51             1.934982  x : 55.7 - 55.75 | y : 37.449999999999996 - 37...
59             1.880164               x : 55.75 - 55.8 | y : 37.3 - 37.375
32             1.791960  x : 55.599999999999994 - 55.65 | y : 37.525 - ...
23             1.780310  x : 55.55 - 55.599999999999994 | y : 37.599999...
63             1.714824  x : 55.75 - 55.8 | y : 37.599999999999994 - 37...
0              1.597609                                            ageFrom
66             1.531590   x : 55.75 - 55.8 | y : 37.824999999999996 - 37.9
54             1.527311              x : 55.7 - 55.75 | y : 37.675 - 37.75
92             1.487873  x : 55.900000000000006 - 55.95 | y : 37.525 - ...
45             1.415187  x : 55.65 - 55.7 | y : 37.75 - 37.824999999999996
5              1.366633                                  distance_luzhniki
43             1.353225  x : 55.65 - 55.7 | y : 37.599999999999994 - 37...
53             1.304370  x : 55.7 - 55.75 | y : 37.599999999999994 - 37...
82             1.219978  x : 55.85 - 55.900000000000006 | y : 37.525 - ...
65             1.153817  x : 55.75 - 55.8 | y : 37.75 - 37.824999999999996
4              1.146833                                   distance_patriki
50             1.146437  x : 55.7 - 55.75 | y : 37.375 - 37.44999999999...
42             1.107965  x : 55.65 - 55.7 | y : 37.525 - 37.59999999999...
6              1.102308                                           age_span
73             1.081886  x : 55.8 - 55.85 | y : 37.599999999999994 - 37...
3              1.053168                                    distance_center
41             1.050189  x : 55.65 - 55.7 | y : 37.449999999999996 - 37...
90             0.894091  x : 55.900000000000006 - 55.95 | y : 37.375 - ...
76             0.882172   x : 55.8 - 55.85 | y : 37.824999999999996 - 37.9
109            0.842320                                             female
30             0.729799  x : 55.599999999999994 - 55.65 | y : 37.375 - ...
71             0.721101  x : 55.8 - 55.85 | y : 37.449999999999996 - 37...
34             0.705987  x : 55.599999999999994 - 55.65 | y : 37.675 - ...
55             0.665584  x : 55.7 - 55.75 | y : 37.75 - 37.824999999999996
61             0.651516  x : 55.75 - 55.8 | y : 37.449999999999996 - 37...
22             0.619755  x : 55.55 - 55.599999999999994 | y : 37.525 - ...
110            0.593067                                               male
1              0.569752                                              ageTo
44             0.528354              x : 55.65 - 55.7 | y : 37.675 - 37.75
60             0.521087  x : 55.75 - 55.8 | y : 37.375 - 37.44999999999...
85             0.509566  x : 55.85 - 55.900000000000006 | y : 37.75 - 3...
75             0.452089  x : 55.8 - 55.85 | y : 37.75 - 37.824999999999996
56             0.444555   x : 55.7 - 55.75 | y : 37.824999999999996 - 37.9
70             0.440972  x : 5

## KNN

In [255]:
knn_model = KNeighborsRegressor(n_neighbors=7, weights='distance', p=1)
knn_model.fit(X_train, y_train)

KNeighborsRegressor(n_neighbors=7, p=1, weights='distance')

In [256]:
y_pred = knn_model.predict(X_test)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 9.1867
R²: 0.8348
MAE: 5.6379


In [257]:
models.append(knn_model)

## SVM

In [214]:
svm_model = SVR(C=200, kernel='rbf')
svm_model.fit(X_train, y_train)

SVR(C=200)

In [215]:
y_pred = svm_model.predict(X_test)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 8.9655
R²: 0.8427
MAE: 5.5109


In [258]:
models.append(svm_model)

## Linear regression

In [217]:
linreg_model = LinearRegression()
linreg_model.fit(X_train, y_train)

LinearRegression()

In [218]:
y_pred = linreg_model.predict(X_test)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 11.6672
R²: 0.7336
MAE: 8.6236


In [259]:
models.append(linreg_model)

## TabNet

In [244]:
!pip -q install pytorch-tabnet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.5/44.5 kB 1.4 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl (121.6 MB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl (56.5 MB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl (124.2 MB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl (196.0 MB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl (176.2 MB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-man

In [249]:
from pytorch_tabnet.tab_model import TabNetRegressor


tabnet_model = TabNetRegressor(verbose=100, seed=SEED)
tabnet_model.fit(X_train=X_train.values, y_train=y_train.values.reshape(-1, 1),
                  eval_set=[(X_val.values, y_val.values.reshape(-1, 1))],
                  patience=300, max_epochs=2000,
                  eval_metric=['rmse'])

/usr/local/lib/python3.10/dist-packages/pytorch_tabnet/abstract_model.py:82: UserWarning: Device used : cpu
  warnings.warn(f"Device used : {self.device}")


epoch 0  | loss: 1080.23682| val_0_rmse: 34.29108|  0:00:00s
epoch 100| loss: 174.1609| val_0_rmse: 15.314  |  0:00:10s
epoch 200| loss: 85.24102| val_0_rmse: 11.04939|  0:00:18s
epoch 300| loss: 48.41201| val_0_rmse: 11.0636 |  0:00:27s
epoch 400| loss: 44.39386| val_0_rmse: 10.6903 |  0:00:37s
epoch 500| loss: 35.90374| val_0_rmse: 9.67587 |  0:00:45s
epoch 600| loss: 30.82354| val_0_rmse: 9.20166 |  0:00:54s
epoch 700| loss: 28.91453| val_0_rmse: 9.67567 |  0:01:04s
epoch 800| loss: 26.22795| val_0_rmse: 9.8764  |  0:01:11s
epoch 900| loss: 26.3332 | val_0_rmse: 9.56045 |  0:01:21s
epoch 1000| loss: 22.65345| val_0_rmse: 9.84485 |  0:01:31s
epoch 1100| loss: 26.04469| val_0_rmse: 9.42005 |  0:01:39s
epoch 1200| loss: 63.74184| val_0_rmse: 14.05094|  0:01:48s
epoch 1300| loss: 21.20982| val_0_rmse: 9.33856 |  0:01:57s
epoch 1400| loss: 21.65337| val_0_rmse: 9.00995 |  0:02:05s
epoch 1500| loss: 21.8536 | val_0_rmse: 8.67851 |  0:02:15s
epoch 1600| loss: 24.51998| val_0_rmse: 9.54106 

/usr/local/lib/python3.10/dist-packages/pytorch_tabnet/callbacks.py:172: UserWarning: Best weights from best epoch are automatically used!
  warnings.warn(wrn_msg)


In [252]:
y_pred = tabnet_model.predict(X_test.values)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 8.5846
R²: 0.8558
MAE: 5.8285


In [305]:
models.append(tabnet_model)

## MLP

In [281]:
mlp_model = MLPRegressor(alpha=1e-2, hidden_layer_sizes=(50, 10), random_state=SEED)
mlp_model.fit(X_train, y_train)

/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


MLPRegressor(alpha=0.01, hidden_layer_sizes=(50, 10), random_state=8642)

In [286]:
# param_grid = [
#         {
#             'activation' : ['logistic', 'tanh', 'relu'],
#             'solver' : ['sgd', 'adam'],
#             'hidden_layer_sizes': [
#                  (10,), (15,), (20,), (20, 10)
#             ]
#         }
#        ]

# mlp_model = GridSearchCV(MLPRegressor(), param_grid, cv=5,
#                            scoring='neg_mean_squared_error')
# mlp_model.fit(X,y)


# print("Best parameters set found on development set:")
# print(mlp_model.best_params_)

/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptro

Best parameters set found on development set:
{'activation': 'tanh', 'hidden_layer_sizes': (15,), 'solver': 'sgd'}


/usr/local/lib/python3.10/dist-packages/sklearn/neural_network/_multilayer_perceptron.py:686: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


In [300]:
mlp_model = MLPRegressor(activation='tanh', solver='sgd', hidden_layer_sizes=(15,), random_state=SEED, max_iter=500)
mlp_model.fit(X_train, y_train)

MLPRegressor(activation='tanh', hidden_layer_sizes=(15,), max_iter=500,
             random_state=8642, solver='sgd')

In [301]:
y_pred = mlp_model.predict(X_test)
rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 8.0720
R²: 0.8725
MAE: 5.5641


In [306]:
models.append(mlp_model)

## Ensemble inference

In [310]:
y_pred = np.zeros(len(X_test))

for model in models[:]:
    if type(model) != TabNetRegressor:
        # print(model.predict(X_test).shape)
        y_pred += model.predict(X_test)
    else:
        # print(model.predict(X_test.values).shape)
        y_pred += model.predict(X_test.values).flatten()

y_pred /= len(models)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 7.2615
R²: 0.8968
MAE: 4.8847


## CatBoost ensemble

In [90]:
catboost_models = []

for seed in [8642, 0, 52, 69, 146]:
    cb_model = CatBoostRegressor(iterations=5000,
                                  max_depth=5,
                                  l2_leaf_reg=3.0,
                                  # learning_rate=0.05,
                                  loss_function='RMSE',
                                   random_seed=seed)

    cb_model.fit(X_train, y_train, eval_set=(X_val, y_val), verbose=200)
    catboost_models.append(cb_model)

0:	learn: 23.2474931	test: 25.0905466	best: 25.0905466 (0)	total: 49.7ms	remaining: 4m 8s
200:	learn: 9.2059050	test: 10.0988787	best: 10.0988787 (200)	total: 409ms	remaining: 9.77s
400:	learn: 7.3095272	test: 8.6953981	best: 8.6953981 (400)	total: 751ms	remaining: 8.61s
600:	learn: 6.2650395	test: 8.2500923	best: 8.2500902 (599)	total: 1.09s	remaining: 7.95s
800:	learn: 5.6319287	test: 7.9897271	best: 7.9887134 (798)	total: 1.45s	remaining: 7.61s
1000:	learn: 5.1784286	test: 7.8348530	best: 7.8348530 (1000)	total: 1.79s	remaining: 7.14s
1200:	learn: 4.8384449	test: 7.6785338	best: 7.6785338 (1200)	total: 2.12s	remaining: 6.72s
1400:	learn: 4.5219718	test: 7.5594688	best: 7.5590512 (1399)	total: 2.48s	remaining: 6.38s
1600:	learn: 4.2742477	test: 7.4719938	best: 7.4708981 (1591)	total: 2.82s	remaining: 5.98s
1800:	learn: 4.0615558	test: 7.4207828	best: 7.4180022 (1785)	total: 3.16s	remaining: 5.62s
2000:	learn: 3.9173181	test: 7.4044367	best: 7.4042745 (1991)	total: 3.52s	remaining: 5.

In [315]:
catboost_models[0].save_model('catboost_task1_mediawise')

In [314]:
y_pred = np.zeros(len(X_test))

for model in catboost_models[:]:
    y_pred += model.predict(X_test)

y_pred /= len(catboost_models)

rmse = mean_squared_error(y_test, y_pred, squared=False)
r2 = r2_score(y_test, y_pred)
mae = mean_absolute_error(y_test, y_pred)

print(f'RMSE: {rmse:.4f}')
print(f'R²: {r2:.4f}')
print(f'MAE: {mae:.4f}')

RMSE: 7.1643
R²: 0.8996
MAE: 4.7262


## Predict

In [162]:
y_pred = ensemble_inference(catboost_models, test_df)
y_pred

array([ 1.12529574e+00,  6.24001800e+00,  9.51544350e+01,  8.00851835e+01,
        1.64144186e+00,  1.64658891e+01,  2.02278227e-01,  2.85231315e+00,
        2.06677682e+01,  1.48550404e+01,  3.15793003e+01,  4.79927107e+01,
        2.56335963e+01,  4.83775563e+01,  2.78841299e+01,  1.54895738e+01,
        1.96298859e-01, -1.84338197e-02,  5.92761125e+00, -1.84338197e-02,
       -1.84338197e-02,  3.27495595e+00,  7.68898101e+00,  4.08104587e+01,
        3.50316335e+01,  3.91846669e+01,  4.23330156e+01,  1.13567467e+00,
        4.28637132e+01,  3.52240929e+01,  3.52240929e+01,  6.74988872e+00,
        1.37447516e+00,  1.39571340e+01,  4.58228800e-01,  5.26969622e+00,
        5.78230001e+00,  2.32992908e+00,  2.66705634e+00,  1.32039666e+01,
        9.86854515e-01,  1.06038833e+01,  1.60930371e+00,  2.25158127e+01,
        1.81091756e+01, -1.11130280e+00,  1.58280398e+01,  4.58919484e+00,
        1.88845180e+01,  3.80681234e+01,  1.54303720e+01,  6.21113933e+01,
        6.22885024e+01, -

## Create a submit

In [100]:
sample_sub = pd.read_csv('/content/sample_submission (6).csv')
sample_sub

hash  value
0    3a94fc3e5c9d8d72     10
1    bcc4e68cbec07f33     10
2    d8da298a5c2b2f27     10
3    5c75b1a1602e33d7     10
4    609bcaed570f5815     10
..                ...    ...
383  4e154970e1c6ae2b     10
384  3c15071c77f49893     10
385  c4576f9dcda42732     10
386  c9c9b7cbe3a925d4     10
387  482c582f88422a17     10

[388 rows x 2 columns]

In [165]:
submit_df = pd.DataFrame()
submit_df['hash'] = source_test_df['hash']
# submit_df['value'] = test_df.apply(lambda row: ensemble_inference(catboost_models, test_df)[0], axis=1)
submit_df['value'] = y_pred
submit_df

hash      value
0    3a94fc3e5c9d8d72   1.125296
1    bcc4e68cbec07f33   6.240018
2    d8da298a5c2b2f27  95.154435
3    5c75b1a1602e33d7  80.085183
4    609bcaed570f5815   1.641442
..                ...        ...
383  4e154970e1c6ae2b   0.653886
384  3c15071c77f49893  33.012148
385  c4576f9dcda42732  21.269329
386  c9c9b7cbe3a925d4  24.766846
387  482c582f88422a17   0.211648

[388 rows x 2 columns]

In [244]:
submit_df.to_csv('sub2.csv', sep =',', lineterminator='\n', index=False)

In [167]:
submit_df.to_csv('sub1.csv', index=False)

# Task 2

## Data processing

In [127]:
bebra = df_scaled.iloc[:, :(config['x_ngroups'] + 2) * (config['y_ngroups'] + 2)]
bebra['max_segm_id'] = bebra.apply(lambda row: np.argmax(row), axis=1)
bebra

x : -inf - 55.55 | y : -inf - 37.3  \
0                                      0   
1                                      0   
2                                      0   
3                                      0   
4                                      0   
...                                  ...   
1542                                   0   
1543                                   0   
1544                                   0   
1545                                   0   
1546                                   0   

      x : -inf - 55.55 | y : 37.3 - 37.375  \
0                                        0   
1                                        0   
2                                        0   
3                                        0   
4                                        0   
...                                    ...   
1542                                     0   
1543                                     0   
1544                                     0   
1545                                     0   
1546                                     0   

      x : -inf - 55.55 | y : 37.375 - 37.449999999999996  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.449999999999996 - 37.525  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.525 - 37.599999999999994  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.599999999999994 - 37.675  \
0                                                     0    
1                                                     0    
2                                                     0    
3                                                     0    
4                                                     0    
...                                                 ...    
1542                                                  0    
1543                                                  0    
1544                                                  0    
1545                                                  0    
1546                                                  0    

      x : -inf - 55.55 | y : 37.675 - 37

In [128]:
bebra['max_segm_id'].value_counts()

max_segm_id
54    228
55    190
45    149
44    140
46     88
58     85
33     78
16     77
38     76
34     60
25     52
35     51
27     48
74     36
53     31
22     25
43     18
23     16
63     14
15     13
56     11
64      8
83      5
72      5
65      4
77      3
61      3
51      3
13      3
84      3
14      3
87      3
26      3
88      3
67      2
76      2
0       2
42      2
52      1
24      1
17      1
75      1
Name: count, dtype: int64

In [124]:
for x in range(config['x_ngroups'] + 2):
    for y in range(config['y_ngroups'] + 2):
        print(df_scaled.iloc[:, x * (config['y_ngroups'] + 2) + y].name)

x : -inf - 55.55 | y : -inf - 37.3
x : -inf - 55.55 | y : 37.3 - 37.375
x : -inf - 55.55 | y : 37.375 - 37.449999999999996
x : -inf - 55.55 | y : 37.449999999999996 - 37.525
x : -inf - 55.55 | y : 37.525 - 37.599999999999994
x : -inf - 55.55 | y : 37.599999999999994 - 37.675
x : -inf - 55.55 | y : 37.675 - 37.75
x : -inf - 55.55 | y : 37.75 - 37.824999999999996
x : -inf - 55.55 | y : 37.824999999999996 - 37.9
x : -inf - 55.55 | y : 37.9 - inf
x : 55.55 - 55.599999999999994 | y : -inf - 37.3
x : 55.55 - 55.599999999999994 | y : 37.3 - 37.375
x : 55.55 - 55.599999999999994 | y : 37.375 - 37.449999999999996
x : 55.55 - 55.599999999999994 | y : 37.449999999999996 - 37.525
x : 55.55 - 55.599999999999994 | y : 37.525 - 37.599999999999994
x : 55.55 - 55.599999999999994 | y : 37.599999999999994 - 37.675
x : 55.55 - 55.599999999999994 | y : 37.675 - 37.75
x : 55.55 - 55.599999999999994 | y : 37.75 - 37.824999999999996
x : 55.55 - 55.599999999999994 | y : 37.824999999999996 - 37.9
x : 55.55 - 55

## CatBoost

In [226]:
X_new.columns.tolist()

['value',
 'ageFrom',
 'ageTo',
 'age_span',
 'age_mean',
 'all',
 'female',
 'male',
 'ab',
 'abc',
 'bc',
 'c']

In [137]:
df_scaled = feature_engineering(df,
                                parse_json=True,
                                drop_zero_cols=False,
                                process_points=False,  #####
                                normalize=False)  ##################
df_scaled

value  ageFrom  ageTo   id  age_span  age_mean    all  female   male  \
0     23.51       25     45  0.0      10.0     17.50   True   False  False   
1      1.20       30     60  0.0      15.0     22.50  False    True  False   
2      4.65       30     60  0.0      15.0     22.50  False    True  False   
3     32.09       30    100  0.0      35.0     32.50  False    True  False   
4     26.12       30    100  0.0      35.0     32.50  False    True  False   
...     ...      ...    ...  ...       ...       ...    ...     ...    ...   
1542  20.55       30     55  0.0      12.5     21.25   True   False  False   
1543  59.32       35    100  0.0      32.5     33.75   True   False  False   
1544  41.30       35    100  0.0      32.5     33.75   True   False  False   
1545  59.15       25     55  0.0      15.0     20.00  False   False   True   
1546  52.66       25     55  0.0      15.0     20.00  False   False   True   

         ab    abc     bc      c  
0     False  False   True  False  
1     False   True  False  False  
2     False   True  False  False  
3     False  False   True  False  
4     False  False   True  False  
...     ...    ...    ...    ...  
1542  False  False   True  False  
1543  False  False  False   True  
1544  False  False  False   True  
1545  False   True  False  False  
1546  False   True  False  False  

[1547 rows x 13 columns]

In [200]:
# X = df_scaled
y = bebra['max_segm_id']

X_train, X_test, y_train, y_test = train_test_split(X.drop(columns=['id']), y, test_size=0.29, random_state=SEED + 1)
X_val, X_test, y_val, y_test = train_test_split(X_test, y_test, test_size=0.52, random_state=SEED + 1)

In [201]:
cb_model = CatBoostClassifier(iterations=5000,
                              max_depth=5,
                              l2_leaf_reg=3.0,
                              # learning_rate=0.05,
                              loss_function='MultiClass',
                              random_seed=SEED)

cb_model.fit(X_train, y_train, eval_set=(X_val, y_val), verbose=100)

0:	learn: 3.6819635	test: 3.6872593	best: 3.6872593 (0)	total: 36.1ms	remaining: 3m
100:	learn: 2.2572406	test: 2.3994289	best: 2.3994289 (100)	total: 2.23s	remaining: 1m 48s
200:	learn: 1.9930380	test: 2.2092874	best: 2.2092874 (200)	total: 3.98s	remaining: 1m 35s
300:	learn: 1.8340718	test: 2.1144377	best: 2.1144377 (300)	total: 5.05s	remaining: 1m 18s
400:	learn: 1.7226762	test: 2.0596000	best: 2.0596000 (400)	total: 6.13s	remaining: 1m 10s
500:	learn: 1.6371747	test: 2.0234600	best: 2.0234600 (500)	total: 7.21s	remaining: 1m 4s
600:	learn: 1.5629914	test: 1.9933233	best: 1.9933233 (600)	total: 8.29s	remaining: 1m
700:	learn: 1.4998634	test: 1.9713273	best: 1.9713273 (700)	total: 9.39s	remaining: 57.6s
800:	learn: 1.4492274	test: 1.9520433	best: 1.9520418 (799)	total: 10.5s	remaining: 55s
900:	learn: 1.4028430	test: 1.9416946	best: 1.9416863 (899)	total: 11.6s	remaining: 52.6s
1000:	learn: 1.3595320	test: 1.9322462	best: 1.9322462 (1000)	total: 12.7s	remaining: 50.6s
1100:	learn: 1.

In [202]:
cb_model.save_model('catboost_for_polygons')

In [203]:
pd.DataFrame({'feature_importance': cb_model.get_feature_importance(Pool(X_train, y_train)),
              'feature_names': X_val.columns}).sort_values(by=['feature_importance'],
                                                           ascending=False).head(60)

feature_importance feature_names
0            31.412682         value
4            14.068921      age_mean
3            13.642172      age_span
1            10.822818       ageFrom
2             8.823310         ageTo
10            7.639998            bc
9             5.206006           abc
5             2.829753           all
11            1.949513             c
7             1.795655          male
6             1.727945        female
8             0.081227            ab

## KNN

In [186]:
X_new = X.drop(columns=['id'])
X_new = (X_new - X_new.mean()) / X_new.std()
X_new

value   ageFrom     ageTo  age_span  age_mean       all    female  \
0     0.031743  0.052411 -0.854526 -0.776246 -0.872346  0.444118 -0.312855   
1    -0.906672  0.833520 -0.148632 -0.356514  0.106560 -2.250198  3.194299   
2    -0.761556  0.833520 -0.148632 -0.356514  0.106560 -2.250198  3.194299   
3     0.392639  0.833520  1.733753  1.322412  2.064370 -2.250198  3.194299   
4     0.141526  0.833520  1.733753  1.322412  2.064370 -2.250198  3.194299   
...        ...       ...       ...       ...       ...       ...       ...   
1542 -0.092762  0.833520 -0.383930 -0.566380 -0.138167  0.444118 -0.312855   
1543  1.538001  1.614630  1.733753  1.112546  2.309096  0.444118 -0.312855   
1544  0.780035  1.614630  1.733753  1.112546  2.309096  0.444118 -0.312855   
1545  1.530850  0.052411 -0.383930 -0.356514 -0.382893 -2.250198 -0.312855   
1546  1.257865  0.052411 -0.383930 -0.356514 -0.382893 -2.250198 -0.312855   

          male        ab       abc        bc         c  
0    -0.285946 -0.084598 -0.728930  0.873770 -0.291201  
1    -0.285946 -0.084598  1.370986 -1.143726 -0.291201  
2    -0.285946 -0.084598  1.370986 -1.143726 -0.291201  
3    -0.285946 -0.084598 -0.728930  0.873770 -0.291201  
4    -0.285946 -0.084598 -0.728930  0.873770 -0.291201  
...        ...       ...       ...       ...       ...  
1542 -0.285946 -0.084598 -0.728930  0.873770 -0.291201  
1543 -0.285946 -0.084598 -0.728930 -1.143726  3.431837  
1544 -0.285946 -0.084598 -0.728930 -1.143726  3.431837  
1545  3.494899 -0.084598  1.370986 -1.143726 -0.291201  
1546  3.494899 -0.084598  1.370986 -1.143726 -0.291201  

[1547 rows x 12 columns]

In [187]:
X_train, X_test, y_train, y_test = train_test_split(X_new, y, test_size=0.3, random_state=SEED)
X_val, X_test, y_val, y_test = train_test_split(X_test, y_test, test_size=0.52, random_state=SEED + 1)

In [188]:
# X_train = X_train.drop(columns=['id'])
X_train_norm = (X_train - X_train.mean()) / X_train.std()
X_train_norm

value   ageFrom     ageTo  age_span  age_mean       all    female  \
959  -0.958867 -1.049403  1.713620  1.817165  1.446664  0.452449 -0.320720   
1234 -0.958867 -1.049403  1.713620  1.817165  1.446664  0.452449 -0.320720   
604   0.060066  0.042230 -0.396871 -0.366771 -0.397538 -2.208150  3.115107   
1009  0.054572 -1.049403 -0.396871 -0.072780 -0.737259  0.452449 -0.320720   
1271 -0.955486 -1.049403  1.713620  1.817165  1.446664  0.452449 -0.320720   
...        ...       ...       ...       ...       ...       ...       ...   
943   1.217618 -1.049403 -0.396871 -0.072780 -0.737259  0.452449 -0.320720   
1386  0.438309  0.042230 -0.631370 -0.576765 -0.640196  0.452449 -0.320720   
379  -0.693885 -1.049403  1.713620  1.817165  1.446664  0.452449 -0.320720   
1151 -0.903081  0.042230 -0.865869 -0.786759 -0.882854  0.452449 -0.320720   
313  -0.957599  0.821968 -0.396871 -0.576765 -0.154880  0.452449 -0.320720   

          male        ab       abc        bc        c  
959  -0.288108 -0.091542  1.358551 -1.127800 -0.29371  
1234 -0.288108 -0.091542  1.358551 -1.127800 -0.29371  
604  -0.288108 -0.091542  1.358551 -1.127800 -0.29371  
1009 -0.288108 -0.091542 -0.735398  0.885863 -0.29371  
1271 -0.288108 -0.091542  1.358551 -1.127800 -0.29371  
...        ...       ...       ...       ...      ...  
943  -0.288108 -0.091542  1.358551 -1.127800 -0.29371  
1386 -0.288108 -0.091542 -0.735398  0.885863 -0.29371  
379  -0.288108 -0.091542  1.358551 -1.127800 -0.29371  
1151 -0.288108 -0.091542 -0.735398  0.885863 -0.29371  
313  -0.288108 -0.091542 -0.735398  0.885863 -0.29371  

[1082 rows x 12 columns]

In [189]:
neigh = NearestNeighbors(n_neighbors=3, radius=0.4)
neigh.fit(X_train)

NearestNeighbors(n_neighbors=3, radius=0.4)

In [190]:
neighbors = neigh.kneighbors(pd.DataFrame(X_test.iloc[0]).T, 5, return_distance=False)
neighbors

array([[  4, 660, 305, 464, 156]])

## Inference

In [230]:
cb_model.predict(X_test.iloc[0:1])

array([[22]])

In [211]:
config = {'min_xval':55.55, 'max_xval':55.95, 'min_yval':37.3, 'max_yval':37.9, 'x_ngroups': 8, 'y_ngroups': 8}

def split_on_intervals(min_val, max_val, n):
    step = (max_val - min_val)/n
    intervals = [min_val+(step*x) for x in range(n+1)]
    return intervals

x_intervals = split_on_intervals(config['min_xval'], config['max_xval'], config['x_ngroups'])
y_intervals = split_on_intervals(config['min_yval'], config['max_yval'], config['y_ngroups'])
x_intervals, y_intervals

([55.55,
  55.599999999999994,
  55.65,
  55.7,
  55.75,
  55.8,
  55.85,
  55.900000000000006,
  55.95],
 [37.3,
  37.375,
  37.449999999999996,
  37.525,
  37.599999999999994,
  37.675,
  37.75,
  37.824999999999996,
  37.9])

In [220]:
y.unique().max()

88

In [221]:
sec_id = 88
x_coord = x_intervals[sec_id % (config['y_ngroups'] + 2)]
y_coord = y_intervals[sec_id // (config['x_ngroups'] + 2)]
x_coord, y_coord

(55.95, 37.9)

In [210]:
df_scaled.iloc[:, 22].name

'x : 55.599999999999994 - 55.65 | y : 37.375 - 37.449999999999996'

In [222]:
''.join(sorted(['a', 'c']))

'ac'

In [231]:
points = []
for i in df['points']:
    for j in i:
        points += [(float(j['lat']), float(j['lon']))]

points_set = set(points)

def calculate_distance(coord1, coord2):
    lat1, lon1 = coord1
    lat2, lon2 = coord2
    return ((lat1 - lat2) ** 2 + (lon1 - lon2) ** 2) ** 0.5

def find_nearest_points(target_coord, points, n):
    distances = [(calculate_distance(target_coord, point), point) for point in points]
    distances.sort()
    return [point for dist, point in distances[:n]]

def cross_product(o, a, b):
    return (a[0] - o[0]) * (b[1] - o[1]) - (a[1] - o[1]) * (b[0] - o[0])

def convex_hull(points):
    # алгоритм Джарвиса
    points = sorted(points)
    if len(points) <= 2:
        return points
    lower = []
    upper = []
    for p in points:
        while len(lower) >= 2 and cross_product(lower[-2], lower[-1], p) <= 0:
            lower.pop()
        lower.append(p)

    for p in reversed(points):
        while len(upper) >= 2 and cross_product(upper[-2], upper[-1], p) <= 0:
            upper.pop()
        upper.append(p)

    return lower[:-1] + upper[:-1]



target_coord = (55.7558, 37.6173)

nearest_points = find_nearest_points(target_coord, points_set, 5)
print(nearest_points)



polygon = convex_hull(nearest_points)
print(polygon)

[(55.756318365036, 37.615726231945), (55.756054677003, 37.61509001255), (55.75855361792, 37.619466017127), (55.757614828761, 37.614121703635), (55.759973712538, 37.619509026461)]
[(55.756054677003, 37.61509001255), (55.757614828761, 37.614121703635), (55.759973712538, 37.619509026461), (55.75855361792, 37.619466017127), (55.756318365036, 37.615726231945)]


In [251]:
def process_income(income_categs: list) -> str:
    if income_categs == ['a'] or income_categs == ['b']:
        return 'ab'
    elif income_categs == ['a', 'c']:
        return 'abc'
    else:
        return ''.join(sorted(income_categs))



def sector_inference(cb_model: CatBoostClassifier, income: list, gender: str,
                     ageFrom: int, ageTo: int, value: float):
    """
      income: NON-EMPTY list containing 'a', 'b', or 'c'
      gender: one of ['male', 'female', 'all']
      ageFrom: lower bound for target audience
      ageTo: upper bound
      value: campaign results
    """
    needed_cols =  ['value',
                    'ageFrom',
                    'ageTo',
                    'age_span',
                    'age_mean',
                    'all',
                    'female',
                    'male',
                    'ab',
                    'abc',
                    'bc',
                    'c']
    str_income = process_income(income)
    if str_income not in needed_cols:
        str_income = 'ab'
    if gender not in needed_cols:
        gender = 'all'
    my_df = dict()
    my_df['value'] = [value]
    my_df['ageFrom'] = [ageFrom]
    my_df['ageTo'] = [ageTo]
    my_df['age_span'] = [(np.array(my_df['ageTo']) - np.array(my_df['ageFrom'])) ** 1/2]
    my_df['age_mean'] = [((np.array(my_df['ageTo']) + np.array(my_df['ageFrom'])) / 2) ** 1/2]
    my_df['all'] = [gender == 'all']
    my_df['male'] = [gender == 'male']
    my_df['female'] = [gender == 'female']
    my_df['ab'] = [str_income == 'ab']
    my_df['abc'] = [str_income == 'abc']
    my_df['bc'] = [str_income == 'bc']
    my_df['c'] = [str_income == 'c']
    print(my_df)

    test_df = pd.DataFrame.from_dict(my_df)
    sec_id = cb_model.predict(test_df).flatten()[0]
    x_coord = x_intervals[sec_id % (config['y_ngroups'] + 2)]
    y_coord = y_intervals[sec_id // (config['x_ngroups'] + 2)]
    return (x_coord, y_coord)


In [253]:
cb_model = CatBoostClassifier()
cb_model.load_model('catboost_for_polygons')
sector_inference(cb_model, income=['a', 'b'], gender='male', ageFrom=44, ageTo=88, value=55.5)

{'value': [55.5], 'ageFrom': [44], 'ageTo': [88], 'age_span': [array([22.])], 'age_mean': [array([33.])], 'all': [False], 'male': [True], 'female': [False], 'ab': [True], 'abc': [False], 'bc': [False], 'c': [False]}


(55.75, 37.675)